In [1]:
import matplotlib.pyplot as plt
import numpy.random as rand
import numpy as np

import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.offline as py

from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
from mpl_toolkits.mplot3d import Axes3D
from IPython.display import Image

# Modèles de flots normalisés

- on va commencer par des flots sans réseau de neurones afin de comprendre les cas simples.

- on passe ensuite au cas avec réseaux de neurones

**Objectif**: *soit $\boldsymbol{x}\in \mathbb{R}^d$, on cherche a déterminer $p_{\theta}(\boldsymbol{x})$ à partir d'exemple: $(\boldsymbol{x}_1,....,\boldsymbol{x}_n)$*

**Modèle**:

$$
p_{\theta}(\boldsymbol{x})=\boldsymbol{z}_K= f_{K}\circ f_{K-1}\circ ... f_{0}(\boldsymbol{z}_0)
$$

## Flots classiques

### Flots affine

Le flot le plus simple est de prendre 

$$
f(\boldsymbol{z})=exp(\boldsymbol{a})\odot \boldsymbol{z} + \boldsymbol{b}
$$

avec $\boldsymbol{a}$ et $\boldsymbol{b}$ les paramètres entrainables et $\odot$ le produit élément par élement.

Si la densité $\boldsymbol{z}_0$ est gaussienne.  $\color{red}{\text{Cette transformation décale et compresse la Gaussienne mais le résultat reste Gaussien}}$.

On peut donc juste obtenir une Gaussienne de dimension $n$.

**Determinant jacobienne**: 

$$
\operatorname{Det}\left(\frac{\partial f}{\partial \boldsymbol{z}}\right)=exp(\boldsymbol{a})
$$

In [2]:
def affine_flot(a,b):
    N=500
    Z0=rand.multivariate_normal([0.0,0.0], [[1.0,0.0],[0.0,1.0]], size=N, check_valid='warn', tol=1e-8)
    Z1=np.zeros((N,2))
    Z1=(np.array([np.exp(a[0]),np.exp(a[1])])[:, np.newaxis]*Z0.T+np.array([b[0],b[1]])[:, np.newaxis]).T
    
    fig = make_subplots(rows=1, cols=1) 
    #ax1.set_ylim([1.5,4.0])
    fig.add_trace(go.Scatter(x=Z0[:,0],y=Z0[:,1],mode="markers",marker_size=8,marker_color='red')) 
    fig.add_trace(go.Scatter(x=Z1[:,0],y=Z1[:,1],mode="markers",marker_size=8,marker_color='blue'))         

    fig.update_layout(showlegend=False)
    fig.show()

In [3]:
@interact(a1=(-0.8,0.8,0.1),a2=(-0.8,0.8,0.1),b1=(-0.8,0.8,0.1),b2=(-0.8,0.8,0.1))
def plot1(a1=0.0,a2=0.0,b1=0.0,b2=0.0):
    affine_flot([a1,a2],[b1,b2])


interactive(children=(FloatSlider(value=0.0, description='a1', max=0.8, min=-0.8), FloatSlider(value=0.0, desc…

### Flots planaires

Une autre solution est de prendre

$$
f(\boldsymbol{z})=\boldsymbol{z} + \boldsymbol{a} \mathrm{tanh}((\boldsymbol{\omega},\boldsymbol{z})+\boldsymbol{b})
$$

avec $\boldsymbol{a}$, $\boldsymbol{\omega}$ et $\boldsymbol{b}$ les paramètres entrainables.

Ce genre de flot compresse ou étend la distribution autour d'un hyperplan de formule $(\boldsymbol{\omega},\boldsymbol{z})+\boldsymbol{b}$.

**Determinant jacobienne**: 

$$
\operatorname{Det}\left(\frac{\partial f}{\partial \boldsymbol{z}}\right)= I_d+(\boldsymbol{a},\mathrm{tanh}^{'}((\boldsymbol{\omega},\boldsymbol{z})+\boldsymbol{b})\boldsymbol{\omega})
$$

In [4]:
def planar_flot(a,b,w):
    N=500
    Z0=rand.multivariate_normal([0.0,0.0], [[1.0,0.0],[0.0,1.0]], size=N, check_valid='warn', tol=1e-8)
    Z1=np.zeros((N,2))
    Z1=Z0+(np.array(a)[:,np.newaxis]*np.tanh(np.dot(np.array(w),Z0.T)+b)).T
    
    fig = make_subplots(rows=1, cols=1) 
    #ax1.set_ylim([1.5,4.0])
    fig.add_trace(go.Scatter(x=Z0[:,0],y=Z0[:,1],mode="markers",marker_size=8,marker_color='red')) 
    fig.add_trace(go.Scatter(x=Z1[:,0],y=Z1[:,1],mode="markers",marker_size=8,marker_color='blue'))         

    fig.update_layout(showlegend=False)
    fig.show()

In [5]:
@interact(a1=(-0.8,0.8,0.1),a2=(-0.8,0.8,0.1),b=(-0.8,0.8,0.1),w1=(-0.8,0.8,0.1),w2=(-0.8,0.8,0.1))
def plot1(a1=0.0,a2=0.0,b=0.0,w1=0.0,w2=0.0):
    planar_flot([a1,a2],b,[w1,w2])


interactive(children=(FloatSlider(value=0.0, description='a1', max=0.8, min=-0.8), FloatSlider(value=0.0, desc…

### Flots radiaux

Une troisième solution: 

$$
f(\boldsymbol{z})= \boldsymbol{z} + \beta h(\alpha,\parallel \boldsymbol{z}-\boldsymbol{z}_0\parallel)(\boldsymbol{z}-\boldsymbol{z}_0)
$$

avec $\alpha$, $\beta$ et $\gamma$ les paramètres entrainables. On prend en général $h(\alpha,r)=\frac{1}{\alpha+r}$

$\color{red}{\text{Cette transformation compresse et étend la distribution autour d'un point $\boldsymbol{z}_0$}}$.


## Flots affines profond


Les flots affines profonds consistent à utiliser des flots affines ou les paramètres sont obtenus à partie de transformation nonlinéaire des entrées.

### RealVNP et Glow

On rappelle que $\boldsymbol{x}\in \mathbb{R}^d$. On rappelle que $d>>1$. 

Dans ce cas, calculer la jacobienne de $f$ et le calcul du determinant peut être très lourd. On va donc faire un choix qui permet:
- un calcul rapide de $\operatorname{Det}\left(\frac{\partial f}{\partial \boldsymbol{z}}\right)$

Pour cela on remarque que: $\color{red}{\text{Le calcul d'un déterminant est très rapide pour une matrice triangulaire}}$.

On obtient donc le choix suivant de flot

$$
    f_{\theta}^k(\boldsymbol{z})=\left\{ \begin{array}{l} y_{1:k}=z_{1:k}\\y_{k+1:d}= z_{k+1:d}\odot exp(s_{\theta}(z_{1:k}))+m_{\theta}(z_{1:k})
    \end{array}\right.
$$

avec $s_{\theta}:\mathbb{R}^k\rightarrow \mathbb{R}^{d-k}$ et $m_{\theta}:\mathbb{R}^k\rightarrow \mathbb{R}^{d-k}$ des réseaux de neurones.

$$
Det\left( \frac{f_{\theta}^k(\boldsymbol{z})}{\partial \boldsymbol{z}}\right) = \left[\begin{array}{l} I_d & 0 \\ .. & diag(exp(s_{\theta}(z_{1:k})))
    \end{array}\right]
$$

L'inversion est aussi très facile avec ce modèle:

$$
    f_{\theta}^k(\boldsymbol{z})=\left\{ \begin{array}{l} z_{1:k}=y_{1:k}\\z_{k+1:d}= (y_{k+1:d}-m_{\theta}(y_{1:k}))\odot exp(-s_{\theta}(y_{1:k}))
    \end{array}\right.
$$


Pour les images notamment, $\color{red}{\text{on ajoute des ingredients multi-échelles}}$.

On peut ajouter une étape de "squeezing" qui passe de $c$ patchs de taille $s\times s$ à $4c$ patchs de taille $\frac{s}{2}\times \frac{s}{2}$.

Pour les images on enchaine
- plusieurs couches affines de transformations,
- des couches de "squeezing",
- et d'autres inégredients,

- Pour le modèle $\color{red}{\text{Glow}}$, on ajoute dans les block de transformation une couche convolutive avant les couches affines.

On peut utiliser pour $y_{k+1:d}$ toute fonction inversible.


## Flots auto-regressifs

Les $\color{red}{\text{modèles auto-régressifs}}$ permettent de modéliser des sequences de données ou une sortie ne dépend que des données issues du passé.

On peut les utiliser pour construire un modèle de densité de probabilité. Par exemple:

$$
 p(\boldsymbol{x})=\prod_{i=1}^D p(x_{i}\mid x_{i-1},...,x_1)=\prod_{i=1}^D p(x_{i}\mid \boldsymbol{x}_{1:i-1})
$$

avec $x_i$ la ième composante de $\boldsymbol{x}$.

Dans un modèle auto-régressif on peut modéliser chaque probabilité avec une Gaussienne dont les moyennes et variances sont des fonctions de $\boldsymbol{x}_{1:i-1}$ ou bien cela peut être directement un réseau de neurones.

**Exemple: MADE**

On choisit un réseau de neurones de type mélange gaussien: 

$$
p(x_{i}\mid \boldsymbol{x}_{1:i-1})=\sum_{k=1}^K \pi_k \mathcal{N}(x_t \mid \mu_k, \Sigma_k)
$$

avec $(\pi_k,\mu_k, \Sigma_k) = f_{\theta}(\boldsymbol{x}_{1:i-1})$ et $f_{\theta}$ un réseau de neurones.

**Exemple: CNN causal**:

$$
p(x_{i}\mid \boldsymbol{x}_{1:i-1})=CNN(\boldsymbol{x}_{1:i-1})
$$

En 2D on a par exemple le PixelCNN.

Si une transformation dans un **modèle de flot normalisant** peut être écrit comme un modèle **auto-régressif**, on parle de $\color{red}{\text{flots auto-régressifs}}$

### Masked Autoregressive Flow

On va donner un première exemple.

On cherche à construire un flot normalisé avec une transformation:

$$
\boldsymbol{x}=f(\boldsymbol{z})
$$

avec $\boldsymbol{z}$ suit une loi $p_z(\boldsymbol{z})$ connue. L'idée est de proposer comme $f$:

$$
f(\boldsymbol{x})=\prod_{i=1}^D p(x_{i}\mid \boldsymbol{x}_{1:i-1})
$$


Le choix effectué est le suivant:
    
$$
p(x_{i}\mid \boldsymbol{x}_{1:i-1})=\mathcal{N}(\boldsymbol{\mu}_{\theta}(\boldsymbol{x}_{1:i-1}), exp(\boldsymbol{\alpha}_{\theta}(\boldsymbol{x}_{1:i-1}))^2)
$$

avec $\mathcal{}$ une Gaussienne, $\mu_{\theta}$ et $\alpha_{\theta}$ des réseaux de neurones. Cela revient à dire que:

$$
x_i=z_i exp(\alpha_{\theta}^i(\boldsymbol{x}_{1:i-1}))+ \mu_{\theta}^i(\boldsymbol{x}_{1:i-1})
$$
avec $z_i$ issu de $p_z(\boldsymbol{z})$.

Evidement on peut calculer les $x_i$ que de façon itératif (ce qui fait que l'échantillonnage de la loi est assez log).

**Avantage**:

- $f$ est inversible:

$$
z_i= (x_i -\mu_{\theta}^i(\boldsymbol{x}_{1:i-1}) ) exp(\alpha_{\theta}^i(\boldsymbol{x}_{1:i-1}))
$$

- On peut calculer facilement

$$
Det\left(\frac{\partial f^{-1}}{\partial \boldsymbol{x}}\right)=exp\left(-\sum_i \alpha_{\theta}^i(\boldsymbol{x}_{1:i-1})\right)
$$

On peut évaluer facilement
$$
p(\boldsymbol{x})=p_z(f^{-1}(\boldsymbol{x})) \left\lvert  Det\left(\frac{\partial f^{-1}}{\partial \boldsymbol{x}}\right)\right\rvert
$$

Il existe une variante appelée "Inverse auto-regressive flow".

## Flot résiduel

Cela revient a prendre une flot de type

$$
f(x)= x+ g_{\theta}(x)
$$

On parle de flot résiduel contractive si la fonction $g_{\theta}()$ est contractive.

Dans **iResNet** on utilise un réseau convolutif correctement normalisé pour être contractif. Cela permet de calculer l'inverse de $g_{\theta}(x)$ par un point fixe.

Pour le déterminant

$$
log\left\lvert det( \partial f(x))\right\lvert =log \left\lvert det( x+ \partial g_{\theta}(x) )\right\lvert =\sum_{i=1}^{\infty} \frac{(-1)^{k+1}}{k}\operatorname{Tr}(\partial g_{\theta}(x)^k) 
$$

La série converge car on est contractif. Les auteurs approches la trace par un estimateur de Hutchinson:

$$
\operatorname{Tr}(\partial g_{\theta}(x)^k) \approx v^t \partial g_{\theta}(x)^k  v
$$

avec $v = \mathcal{N}(0,I_d)$.

## Exemple rapide

Images tirées de l'exemple de K. Murphy: probabilistic machine learning, advanced topics.

Distribution initiale (Gaussienne), et objectif

<img src="beginning.png" alt="Drawing" style="width: 400px;"/>

Résultat et objectif

<img src="res.png" alt="Drawing" style="width: 400px;"/>

Comportement en fonction des couches:

<img src="layers.png" alt="Drawing" style="width: 800px;"/>

## Applications

On veut résoudre:
    
$$
\left\{\begin{array}{l}
\partial_t \mathbf{U}=\mathcal{N}(\mathbf{U},\partial_x \mathbf{U}, \partial_{xx} \mathbf{U},\boldsymbol{\beta}) \\
\mathbf{U}_h(t,x)=g(x),\quad \forall x \in \partial \Omega\\
\mathbf{U}(0,x)=\mathbf{U}_0(x,\boldsymbol{\alpha})
\end{array}\right.
$$

**Idée des PINNs**:

La premières idée des PINNs vient du constat que par construction les réseaux de neurones sont des fonctions plusieurs fois dérivables par rapport à leurs poids et leurs entrées. 

Par conséquent les réseaux de neurones dont les dérivées sont facilement évaluable par différentiation automatique forme des candidats naturels d'approximation d'EDP. 

On décrit donc la solution comme un réseau: $\mathbf{U}_{\theta}(t,x)$.

**Que minimise t'on ?**

\begin{equation}\label{eq:chap67_MC}
\operatorname{min}_{\theta} J_r(\theta)+J_b(\theta)+J_i(\theta)
\end{equation}
avec
\begin{equation}\label{eq:chap67_MC1}
 J_r(\theta)=\int_0^T\int_{\Omega}\parallel \partial_t\mathbf{U}_{\theta}(t,x)-\mathcal{L}(\mathbf{U}_{\theta},\partial_x \mathbf{U}_{\theta}, \partial_{xx} \mathbf{U}_{\theta},\boldsymbol{\beta})(t,x)\parallel_2^2 dxdt 
\end{equation}
et
\begin{equation}\label{eq:chap67_MC2}
J_b(\theta)=\int_0^T \int_{\partial \Omega} \parallel \mathbf{U}_{\theta}(t,x)-g(x)\parallel_2^2 dxdt,\quad J_i(\theta)=\int_{\Omega} \parallel \mathbf{U}_{\theta}(0,x)-\mathbf{U}_{0}(x)\parallel_2^2 dx
\end{equation}

On approche ces intégrales par **Monte-Carlo**. On note $\boldsymbol{\mu}=(g(x),\mathbf{U}_{0}(x),\boldsymbol{\beta})$

L'idée centrale est simplement de concentrer les poids $(t_i,x_i)$ tirés aléatoirement pour approche l'intégrale de la loss la ou l'erreur du réseau est la plus grande. Pour cela on va passer par **l'échantillonnage préférentiel**.

On définit
$$
r_{\theta}(x,t,\boldsymbol{\mu})=\parallel \partial_t\hat{\mathbf{U}}_{\theta}(t,x,\boldsymbol{\mu})-\mathcal{L}(\hat{\mathbf{U}}_{\theta},\partial_x \hat{\mathbf{U}}_{\theta}, \partial_{xx} \hat{\mathbf{U}}_{\theta},\boldsymbol{\beta})(t,x)\parallel_2^2
$$

On a donc 

$$
\mathcal{J}(\theta)=\int_{V_{\mu}}\int_0^T\int_{\Omega}r_{\theta}(x,t,\boldsymbol{\mu}) dxdt d\boldsymbol{\mu} 
$$

$$
\mathcal{J}(\theta)=\int_{V_{\mu}}\int_0^T\int_{\Omega}r_{\theta}(x,t,\boldsymbol{\mu}) dxdt d\boldsymbol{\mu}= \int_{V_{\mu}}\int_0^T\int_{\Omega}\frac{r_{\theta}(x,t,\boldsymbol{\mu})}{p(t,x,\boldsymbol{\mu})}p(t,x,\boldsymbol{\mu})dxdt d\boldsymbol{\mu} 
$$


Comment on approche $p$ ? 

On construit $p_{\theta^*}(t,x,\boldsymbol{\mu})$ un **flot normalisé** qui satisfait:

$$
\operatorname{min}_{\theta^*} D_{KL}(r_{\theta}(x,t,\boldsymbol{\mu})\mid \mid p_{\theta^*}(t,x,\boldsymbol{\mu}))
$$

Dans l'algo d'entrainement: on alterne entrainement du PINN's et celui du flot normalisé.